In [ ]:
%pylab inline

In [ ]:
import re
import string
import math

# TP3 - Filtre Anti-spam



Le but d’un filtre anti-spam est d’identifier et d’éliminer les e-mails indésirables avant qu’ils n’arrivent dans la boîte aux lettres. Pour estimer la probabilité qu'un courrier soit un spam, on se ramène à observer des événements élémentaires, typiquement la présence d'un mot donné dans le message.

Pour une meilleure précision, ce filtre est construit non à partir d’un vocabulaire prédéfini mais à partir des mots présents dans la base d’exemples.  On considère en tout deux bases d’exemples : une base de mail valides (les “hams”) et une base de mails indésirables (les “spams”). Le programme construit une représentation statistique de ces deux ensembles, en extrayant des mots permettant de différencier au mieux la classe des hams de la classe des spams. La présence ou non de ces mots typiques dans un message inconnu permet ensuite de le classer comme valide ou comme indésirable.


### Base d’apprentissage

Il est possible d’utiliser les messages présents dans votre boite personnelle (repertoire `~/Maildir`). 
Les différents messages qui vous sont adressés apparaissent sous la forme de fichiers textes (dont les noms sont un peu long) lisibles dans les répertoires `cur`, `new` et `tmp`. 
Néanmoins, les messages de votre boîte personnelle ont déjà été filtrés et peu de spams y apparaissent.

Pour construire une base d’apprentissage, il faut disposer d’un ensemble d’exemples de spams et de non spams

Nous utiliserons donc plutôt une base de messages publique pour tester notre algorithme :
http://spamassassin.apache.org/old/publiccorpus/

Nous utiliserons comme base d’apprentissage :
 - easy_ham_2 (http://spamassassin.apache.org/old/publiccorpus/20030228_easy_ham_2.tar.bz2) : 1400 messages non-spams
 - spam_2 (http://spamassassin.apache.org/old/publiccorpus/20030228_spam_2.tar.bz2) : 1397  messages spam.
 
Pour les tests, nous prendrons : 

http://spamassassin.apache.org/old/publiccorpus/20030228_spam.tar.bz2

http://spamassassin.apache.org/old/publiccorpus/20030228_easy_ham.tar.bz2

Chaque base d’apprentissage est un répertoire. Chacun de ces répertoires contient une série de messages (e-mails), chaque fichiers correspondant à un message différent.

Téléchargez les bases et décompressez-les dans un répertoire de votre choix.  
Le filtre anti-spam doit apprendre à partir de ces exemples 


### 1. Extraire le contenu des messages 

Les courriers électroniques utilisent un format standardisé.

* *En-tête* — structuré en champs tels que From, To, CC, Subject, Date, et autres informations à propos du courrier
* *Corps* — Le contenu du message : texte non structuré. 

L’en-tête est séparé du corps par une ligne vide


#### 1.1 Afficher le contenu d’un fichier
Ecrire une fonction python qui ouvre un fichier mail et :
* affiche le sujet du mail 
* affiche le contenu du message  (le corps)

La fonction prend en paramètre le nom du fichier 

Testez votre programme sur plusieurs fichiers des dossiers `spam_2` et `easy_ham_2`.


#### 1.2 Afficher le contenu d’un répertoire

Ecrire une fonction qui affiche la liste des sujets des messages contenus dans un repertoire `rep` fourni en paramètre.

Pour récupérer la liste des fichiers du répertoire, vous ferez appel à la fonction `popen` de la librairie `os` qui permet de récupérer dans une liste le résultat d’une commande unix.

    f = os.popen('ls '+rep,'r')
    liste = f.readlines()

Chaque fichier de la liste doit ensuite être ouvert et le contenu du champ `‘Subject:’` affiché.

La fonction prend en paramètre le nom du répertoire.

Testez votre fonction sur un des répertoires de mails ham ou spam.

**remarque** : pour supprimer le caractère `'\n'` à la fin d’un texte `s` : 

    s[:-1]


#### 1.3 Extraire les mots d’un message
Les termes utilisés dans un message sont situés dans le sujet et le corps du mail. 

Ecrire une fonction qui retourne la liste des termes présents dans un message. 
* A l’aide d’une expression régulière, vous devez découper en liste de mots le sujet et les ligne du corps
* pensez à unifier la casse des mots rencontrés (tout en minuscules par exemple)
* pour chaque mot extrait, l’ajouter à la liste des termes du message s’il n’y est pas déjà.

La fonction prend en paramètre le nom du fichier.

Vous testerez cette fonction en affichant la liste des termes présents dans plusieurs fichiers ham et spam.


#### 1.4 Construction d’un dictionnaire de termes
On souhaite maintenant compter la fréquence des termes utilisés dans les hams et dans les spams. Nous allons pour cela construire un dictionnaire.

Ecrire une fonction qui :
* initilise un dictionnaire vide
* parcourt le contenu d’un répertoire. Pour chaque message rencontré:
  * extrait la liste des termes à l’aide de la fonction précédente
  * teste pour chaque mot de la liste s’il est présent dans le dictionnaire. 
    * Si c’est le cas, incrémente le compteur, 
    * sinon initialise le compteur à 1. 

La fonction prend en paramètres le nom du répertoire et retourne le dictionnnaire.

Pour tester cette fonction, 
1. Appliquer la fonction sur les répertoires `'easy_ham_2'`, et nommer le dictionnaire obtenu `dico_ham`
1. Appliquer la fonction sur les répertoires `'spam_2'`, et nommer le dictionnaire obtenu `dico_spam`
1. Afficher les deux dictionnaires obtenus


### 2. Classifieur du max de vraisemblance


Pour déterminer si un message inconnu est un ham ou un spam, la décision repose sur :

$$\text{réponse}= \underset{k \in \{\text{ham},\text{spam}\}}{\text{argmax}} p(d|k)$$

où $d$ représente un message. 


#### 2.1 Formulation simple

Soient $t_1$, ..., $t_m$ les termes du vocabulaire présents dans le mesage inconnu $d$. On utilise fréquemment une formule approchée ne considérant que les probabilités associées aux termes présents dans le message, soit :

  $$ p(d|\text{spam}) = p(t_1, ..., t_m|\text{spam}) \simeq \prod_{i = 1}^m p(t_i|\text{spam}) $$
  
  $$ p(d|\text{ham}) = p(t_1, ..., t_m|\text{ham}) \simeq \prod_{i = 1}^m p(t_i|\text{ham}) $$


##### 2.1.1 Extraction du vocabulaire commun
Il est nécessaire pour appliquer la formule de considérer uniquement les termes présents à la fois dans la base de hams et dans la base de spams.

Ecrire une fonction qui retourne la liste des termes communs à partir des dictionnaires `dico_ham` et `dico_spam`.

Cette liste sera nommée `vocabulaire`.



##### 2.1.2 Calcul des probas

Ecrire une fonction qui, à partir d’un dico, d’un vocabulaire et d’un entier (nombre de messages) retourne un dictionnaire contenant les probabilités d’apparition des différents termes du vocabulaire.

Utiliser cette fonction pour générer deux dictionnaires `p_ham` et `p_spam`. Vérifier que les valeurs des probabilités sont bien comprises entre 0 et 1.


##### 2.1.3 Classification d’un message

Ecrire une fonction qui, à partir d'un nom de fichier, du vocabulaire et des probas `p_ham` et `p_spam` “prédit” si un message est un ham ou un spam (En utilisant les formules de la partie 2.1). 

$$ \text{prediction}(d) = \arg\max_{\text{spam},\text{ham}}p(d|\text{spam}),p(d|\text{ham}) $$

Pensez à utiliser la fonction de la question 1.3 qui extrait les termes présents dans le message.
 
Vous testerez cette fonction dans le programme principal en l’appliquant à des messages de type ham et de type spam extraits de la base d’apprentissage.



#### 2.2 formulation vectorielle

Pour chaque terme de vocabulaire $t$, soit $x[t]$ qui vaut 1 si le terme est présent dans le message et 0 sinon.

Selon l’hypothèse d’indépendance des probas sur les termes, la formule de la vraisemblance vaut:

$$p(x|\text{spam}) = \prod_t x[t] \times  p(t|\text{spam}) + (1-x[t]) \times (1-p(t|\text{spam})$$

$$p(x|\text{ham}) = \prod_t x[t] \times  p(t|\text{ham}) + (1-x[t]) \times (1-p(t|\text{ham})$$

Pour des raisons de précision numérique, on utilisera de préférence le log de la proba soit :

$$\log p(x|\text{spam}) = \sum_t \log(x[t] \times  p(t|\text{spam}) + (1-x[t]) \times (1-p(t|\text{spam}))$$

$$\log p(x|\text{ham}) = \sum_t \log(x[t] \times  p(t|\text{ham}) + (1-x[t]) \times (1-p(t|\text{ham}))$$


##### 2.2.1 “Vectorisation” d’un message inconnu

Ecrire une fonction qui, à partir d’un nom de fichier et du vocabulaire, construit un dictionnaire `x` associant à chaque terme `t` la valeur 1 si le terme est présent dans le message et 0 sinon. Pensez à utiliser la fonction de la question 1.3

Vous testerez cette fonction en vérifiant que le dictionnaire `x` contient bien des 0 et des 1.


##### 2.2.2 Classification d’un message

Ecrire une fonction qui, à partir du dictionnaire `x` et des probas `p_ham` et `p_spam` “décide” si un message est un ham ou un spam (En utilisant les formules de la section 2.2)
 
Vous testerez cette fonction en l’appliquant à des messages de type ham et de type spam extraits de la base d’apprentissage.


#### 2.3 Tester la précision du classifieur

Testez le taux de bonne classification de vos deux classifieurs sur les bases d’apprentissage `spam_2` et `easy_ham_2` puis sur les bases de test `spam` et `easy_ham`.

Comparez à la fois l’efficacité et le temps de calcul pour les deux cas.
